This notebook will demo the 4 P instant audio feedback.

In [95]:
'''Import necessary libraries'''
'''Make the necessary imports'''
import os
import numpy as np
from numpy import mean
import random
from math import ceil, floor
import json
from scipy.signal import hamming 
import pandas as pd
import numpy as np
import sys
import parselmouth
import matplotlib.pyplot as plt
from scipy.io import wavfile
from scipy.signal import medfilt
from vosk import Model, KaldiRecognizer
import math
from parselmouth.praat import call

In [96]:
'''Accessing Audio files. This needs to be adjusted'''
audio_files = sorted([file for file in os.listdir("/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/")
                  if '.wav' in file])
txt_files = sorted([file for file in os.listdir("/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/")
                  if '.txt' in file])

common_prefix = set([i.replace('.txt', "") for i in txt_files]).intersection(set([i.replace('.wav', "") for i in audio_files]))

txt_files = sorted([i for i in txt_files if i.replace('.txt', '') in common_prefix])
audio_files = sorted([i for i in audio_files if i.replace('.wav', '') in common_prefix])
audio_files = ["/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/"+i for i in audio_files]

In [97]:
emotional_files = ['/home/ubuntu/emotional_sounds/wav/Dr_Evil_Laughing_Scene.wav',
                  "/home/ubuntu/emotional_sounds/wav/Will's_Father_leaves.wav",
                  "/home/ubuntu/emotional_sounds/wav/The_Great_Dictator.wav"]

podcast_files = ["/home/ubuntu/pause_audios/wav/podcast_15150.wav",
                 "/home/ubuntu/pause_audios/wav/podcast_16136.wav",
                 "/home/ubuntu/pause_audios/wav/podcast_17021.wav",
                 "/home/ubuntu/pause_audios/wav/podcast_15586.wav",
                 "/home/ubuntu/pause_audios/wav/podcast_16601.wav"
                ]

## Identify Pause

In [98]:
# Compute the short-term energy and spectral centroid of the signal
def ShortTimeEnergy(signal, windowLength,step):
    signal = signal / max(signal)
    curPos = 1;
    L = len(signal)
    
    from math import floor, ceil
    numOfFrames = floor((L-windowLength)/step) + 1;
    
    E = np.zeros((numOfFrames,1))
    
    for i in range(numOfFrames):
        window = signal[ceil(curPos):ceil(curPos+ windowLength-1)];
        E[i] = (1/(windowLength)) * sum(abs(np.power(window,2)));
        curPos = curPos + step;
        
    return E

# Compute the short-term energy and spectral centroid of the signal
def SpectralCentroid(signal, windowLength, step, fs):
    windowLength = ceil(windowLength);
    
    signal = signal / max(abs(signal));
    
    curPos = 0;
    L = len(signal);
    numOfFrames = floor((L-windowLength)/step) + 1;
    
    H = hamming(windowLength);
    m = np.array([(fs/(2*windowLength))*float(i+1) for i in range(windowLength)])
    m = m.transpose()
    C = np.zeros((numOfFrames,1))
    
    for i in range(numOfFrames):

        # Broadcast length check
        broadcast_length = len(signal[ceil(curPos):ceil(curPos+windowLength)])

        window = H[0:broadcast_length]*signal[ceil(curPos):ceil(curPos+windowLength)]
        FFT = (abs(np.fft.fft(window,2*windowLength)));
        FFT = FFT[0:windowLength];  
        FFT = FFT / max(FFT);
        C[i] = sum(m*FFT)/sum(FFT);
        if (sum(np.power(window,2))<0.010):
            C[i] = 0.0

        curPos = curPos + step;
        
    C = C / (fs/2);
    
    return C

def findMaxima(f, step):
    
    countMaxima = 0

    Maxima = [[], []]

    for i in range(0, len(f)-step-1):  # for each element of the sequence:
        if (i>step):
            if (( mean(f[i-step:i])< f[i]) and ( mean(f[i+1:i+step+1])< f[i])):  
                # IF the current element is larger than its neighbors (2*step window)
                # --> keep maximum:
                countMaxima = countMaxima + 1;
                Maxima[0].append(i);
                Maxima[1].append(f[i]);
        else:
            if (( mean(f[0:i+1])<= f[i]) and ( mean(f[i+1:i+step])< f[i])):
                # IF the current element is larger than its neighbors (2*step window)~
                # --> keep maximum:
                countMaxima = countMaxima + 1;
                Maxima[0].append(i);
                Maxima[1].append(f[i]);
                

    #
    # STEP 2: post process maxima:
    #

    MaximaNew = [[], []];
    countNewMaxima = 0;
    i = 0; # Python indexing starts from 0
    while (i<countMaxima-1):
        # get current maximum:

        curMaxima = Maxima[0][i];
        curMavVal = Maxima[1][i];

        tempMax = [Maxima[0][i]];
        tempVals = [Maxima[1][i]];

        # search for "neighbourh maxima":
        while ((i<countMaxima-1) and ( Maxima[0][i+1] - tempMax[-1] < step / 2)):
            tempMax.append(Maxima[0][i]);
            tempVals.append(Maxima[1][i]);
            i = i + 1;

        # find the maximum value and index from the tempVals array:
        # MI = findCentroid(tempMax, tempVals); MM = tempVals(MI);

        MM = max(tempVals);
        MI = np.argmax(tempVals);

        if (MM>0.02*mean(f)): # if the current maximum is "large" enough:
            # keep the maximum of all maxima in the region:
            MaximaNew[0].append(tempMax[MI]) 
            MaximaNew[1].append(f[MaximaNew[0][countNewMaxima]]);

            countNewMaxima = countNewMaxima + 1;   # add maxima

        tempMax = [];
        tempVals = [];

        ## Update the counter
        i = i + 1;

    Maxima = MaximaNew;
    countMaxima = countNewMaxima;   
    
    return (Maxima, countMaxima)


'''Main function call'''
def pause_main(file_location):

    '''Read the file'''
    fs, x = wavfile.read(file_location)

    N = len(x);
    t = [i/fs for i in range(N)]; # Transform into time domain


    # Window length and step (in seconds)
    win = 0.050
    step = 0.050

    ## Threshold Estimation
    Weight = 5 # Used in the threshold estimation method

    Eor = ShortTimeEnergy(x, win*fs, step*fs)
    # Compute spectral centroid
    Cor = SpectralCentroid(x, win*fs, step*fs, fs)

    # Apply median filtering in the feature sequences (twice), using 5 windows:
    # (i.e., 250 mseconds)
    E = medfilt(medfilt([i[0] for i in Eor.tolist()], 5), 5)

    C = medfilt(medfilt([i[0] for i in Cor.tolist()], 5), 5)

    # Get the average values of the smoothed feature sequences:
    E_mean = np.mean(E);
    Z_mean = np.mean(C);

    # Find energy threshold
    [HistE, X_E] = np.histogram(E, bins = round(len(E) / 10));  # histogram computation
    X_E = np.array([(X_E[idx]+X_E[idx+1])/2 for idx in range(len(X_E)-1)])

    [MaximaE, countMaximaE] = findMaxima(HistE, 3);

    if (len(MaximaE[0])>=2): # if at least two local maxima have been found in the histogram:
        T_E = (Weight*X_E[MaximaE[0][0]]+X_E[MaximaE[0][1]]) / (Weight+1); # ... then compute the threshold as the weighted average between the two first histogram's local maxima.
    else:
        T_E = E_mean / 2;

    # Find spectral centroid threshold:
    [HistC, X_C] = np.histogram(C, round(len(C) / 10));
    X_C = np.array([(X_C[idx]+X_C[idx+1])/2 for idx in range(len(X_C)-1)])

    [MaximaC, countMaximaC] = findMaxima(HistC, 3);
    if (len(MaximaC[0])>=2):
        T_C = (Weight*X_C[MaximaC[0][0]]+X_C[MaximaC[0][1]]) / (Weight+1);
    else:
        T_C = Z_mean / 2;

    Flags1 = (E>=T_E);
    Flags2 = (C>=T_C);
    
    '''Check if array broadcasting doesn't have issues.'''
    if Flags1.shape[0]!=Flags2.shape[0]:
        if Flags1.shape[0]>Flags2.shape[0]:
            Flags1 = Flags1[0:Flags2.shape[0]]

        if Flags2.shape[0]>Flags1.shape[0]:
            Flags2 = Flags1[0:Flags1.shape[0]]
        
    flags = Flags1 & Flags2

    # %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
    # %  SPEECH SEGMENTS DETECTION
    # %%%%%%%%%%%%%%%%%%%%%%%%%%%%%%
    
    count = 0;
    WIN = 5;
    Limits = [[], []];
    while (count < len(flags)): # while there are windows to be processed:
        # initilize:
        curX = [];
        countTemp = 1;
        # while flags=1:
        while ((flags[count]==True) and (count < len(flags))):
            if (countTemp==1): # if this is the first of the current speech segment:
                Limit1 = round((count+1-WIN)*step*fs)+1; # set start limit:
                if (Limit1<1):
                    Limit1 = 1;         

            count = count + 1; # increase overall counter
            
            if count==len(flags):
                break
            
            countTemp = countTemp + 1; # increase counter of the CURRENT speech segment

        if (countTemp>1): # if at least one segment has been found in the current loop:
            Limit2 = round((count+1+WIN)*step*fs); # set end counter
            if (Limit2>len(x)):
                Limit2 = len(x);

            Limits[0].append(Limit1-1);
            Limits[1].append(Limit2-1);

        count = count + 1; # increase overall counter

    # %%%%%%%%%%%%%%%%%%%%%%%
    # % POST - PROCESS      %
    # %%%%%%%%%%%%%%%%%%%%%%%
    # % A. MERGE OVERLAPPING SEGMENTS:
    RUN = 1;
    while RUN==1:
        RUN = 0;
        for i in range(0, len(Limits[0])-1): # for each segment
            if (Limits[1][i]>=Limits[0][i+1]):
                RUN = 1;
                Limits[1][i] = Limits[1][i+1];
                Limits[0].pop(i+1)
                Limits[1].pop(i+1)
                break

    # B. Get final segments:
    segments = [];
    for i in range(0, len(Limits[0])):
        segments.append(x[Limits[0][i]:Limits[1][i]]); 

    # Record pause positions
    pause_positions = [[0 for i in range(len(Limits[0]))], [0 for i in range(len(Limits[0]))]]

    for i in range(0, len(segments)): # Number of segments = Number of Limits
        if i==0:
            if Limits[0][0]!=0:
                pause_positions[0][0] = 0;
                pause_positions[1][0] = Limits[0][0];
            else:
                pause_positions[0][0] = Limits[0][0];
                pause_positions[1][0] = Limits[1][0];

        else:
            pause_positions[0][i] = Limits[1][i-1];
            pause_positions[1][i] = Limits[0][i];

    # Print pause positions and durations
    pause_info = []
    for i in range(0, len(pause_positions[0])):        
        pause_info.append({
                'pause_start': t[pause_positions[0][i]],
                'pause_finish': t[pause_positions[1][i]],
                'pause_duration': t[pause_positions[1][i]] - t[pause_positions[0][i]]
            })
    
    return pause_info, t

In [99]:
# def pause_score(file_location):
    
#     return 

In [100]:
file_location = audio_files[54]
pause_info = pause_main(file_location)

/home/ubuntu/miniconda3/envs/python_main/lib/python3.6/site-packages/ipykernel_launcher.py:42: RuntimeWarning: invalid value encountered in true_divide


In [101]:
pause_info

([{'pause_start': 0.0, 'pause_finish': 0.65, 'pause_duration': 0.65},
  {'pause_start': 4.1499375,
   'pause_finish': 4.3,
   'pause_duration': 0.15006249999999977},
  {'pause_start': 7.8999375,
   'pause_finish': 7.95,
   'pause_duration': 0.05006250000000012},
  {'pause_start': 12.0999375,
   'pause_finish': 12.65,
   'pause_duration': 0.550062500000001},
  {'pause_start': 13.6999375,
   'pause_finish': 13.75,
   'pause_duration': 0.05006249999999923},
  {'pause_start': 18.2499375,
   'pause_finish': 18.7,
   'pause_duration': 0.4500624999999978},
  {'pause_start': 23.9499375,
   'pause_finish': 24.05,
   'pause_duration': 0.10006249999999994},
  {'pause_start': 26.8999375,
   'pause_finish': 27.0,
   'pause_duration': 0.10006249999999994},
  {'pause_start': 28.2999375,
   'pause_finish': 28.5,
   'pause_duration': 0.20006250000000136},
  {'pause_start': 32.0999375,
   'pause_finish': 32.1,
   'pause_duration': 6.249999999852207e-05},
  {'pause_start': 35.8999375,
   'pause_finish': 

In [102]:
import IPython
IPython.display.Audio(file_location)

In [103]:
def pause_feedback(pause_score):
    
    text = ''
    text_list = []
    if pause_score>=90:
        temp_lst = ['Great job!', 'Great work!', 'Excellent!', 'Bravo!', 'Amazing work!', 'Exemplary work!', 
                   ]
        temp_lst2 = ['You are doing well in reducing awkward pauses.', 'The less awkward pauses you have, the better your speech.',
                    'With fewer awkward pauses the flow of your speech is not broken and its easy to understand.',
                    'You really prepared your speech well as visible by your lack of awkward pauses.']
        random.shuffle(temp_lst)
        random.shuffle(temp_lst2)
        text += """{} {} But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You will notice that there is often a pause before introducing Amitabh Bachhan in order to create suspense. Now you too practice introducing pauses purposefully to increase the quality of your speech.""".format(temp_lst[0], temp_lst2[0])
        text_list += [temp_lst[0], temp_lst2[0], """But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You will notice that there is often a pause before introducing Amitabh Bachhan in order to create suspense. Now you too practice introducing pauses purposefully to increase the quality of your speech."""]
    
    elif pause_score>=80:
        temp_lst = ['Good job!', 'Good work!', 'Well done!', 'Nice!']
        temp_lst2 = ['You are doing well but can improve in reducing awkward pauses.', 
                     'Your speech flow is good because you lack large number of awkward pauses. Nonetheless, you can do better.',
                    'You are on path of success, work even more to reduce the number of clumsy pauses in your speech.',
                    'Work on your speech some more until you minimize the number of unexpected pauses you take.']
        random.shuffle(temp_lst)
        random.shuffle(temp_lst2)
        text += """{} {} When you have unexpected pauses then it can distract your audience. A pause can be powerful if it is planned well in speech such as an introduction (Here comes Mr. Akshay), or an exclamation (Wow!). However, unplanned pauses breaks your sentences in between and confuses your audience.""".format(temp_lst[0], temp_lst2[0])
        text_list += [temp_lst[0], temp_lst2[0], """When you have unexpected pauses then it can distract your audience. A pause can be powerful if it is planned well in speech such as an introduction (Here comes Mr. Akshay), or an exclamation (Wow!). However, unplanned pauses breaks your sentences in between and confuses your audience."""]
        
    elif pause_score<80:
        temp_lst = ['Satisfactory!', 'OK!', 'Not great!', 'You can do better!']
        temp_lst2 = ['You need to improve in reducing clumsy pauses.', 
                     'You have unusually large number of unexpected pauses in your speech.',
                    'You should work more to reduce the number of long and short pauses from your speech.',
                    'Your quality of speech can be improved by reducing the number of these awkward pauses.']
        random.shuffle(temp_lst)
        random.shuffle(temp_lst2)
        text += """{} {} A large number of pauses in a speech is a sign of either lack of confidence or lack of preparation. Sometimes both. Try to practice your speech in advance in front of mirror or members of your family without any notes to improve confidence. Having less unwanted pauses will make you appear more confident in front of your audience and will also make you easy to understand.""".format(temp_lst[0], temp_lst2[0])
        text_list += [temp_lst[0], temp_lst2[0], """A large number of pauses in a speech is a sign of either lack of confidence or lack of preparation. Sometimes both. Try to practice your speech in advance in front of mirror or members of your family without any notes to improve confidence. Having less unwanted pauses will make you appear more confident in front of your audience and will also make you easy to understand."""]
        
    return text, text_list

In [104]:
for file_location in audio_files:
    pause_info, time_arr = pause_main(file_location)
    print('------------')
    print(file_location)
    short_pauses = [(i['pause_start'], i['pause_finish'], i['pause_duration']) for i in pause_info if (i['pause_duration']>=0.5 and i['pause_duration']<1)]
    long_pauses = [(i['pause_start'], i['pause_finish'], i['pause_duration']) for i in pause_info if (i['pause_duration']>=1)]

    pause_score = np.round(((1 - sum([i['pause_duration'] for i in pause_info])/time_arr[-1]))*100)

    print(short_pauses)
    print(long_pauses)
    
    if len(short_pauses)<=1 and len(long_pauses)<=1:
        print('You took {} short pause and {} long pause.'.format(len(short_pauses), len(long_pauses)))
    elif len(short_pauses)<=1:
        print('You took {} short pause and {} long pauses.'.format(len(short_pauses), len(long_pauses)))
    elif len(long_pauses)<=1:
        print('You took {} short pauses and {} long pause.'.format(len(short_pauses), len(long_pauses)))
    else:
        print('You took {} short pauses and {} long pauses.'.format(len(short_pauses), len(long_pauses)))
        
    text = pause_feedback(pause_score)
    print(text)
        
    print(pause_score)

/home/ubuntu/miniconda3/envs/python_main/lib/python3.6/site-packages/ipykernel_launcher.py:42: RuntimeWarning: invalid value encountered in true_divide


------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_100.wav
[(0.0, 0.9, 0.9), (23.7499375, 24.45, 0.7000624999999978)]
[]
You took 2 short pauses and 0 long pause.
('Excellent! You are doing well in reducing awkward pauses. But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You will notice that there is often a pause before introducing Amitabh Bachhan in order to create suspense. Now you too practice introducing pauses purposefully to increase the quality of your speech.', ['Excellent!', 'You are doing well in reducing awkward pauses.', 'But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome th

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_108.wav
[(24.7499375, 25.45, 0.7000624999999978), (26.2999375, 27.15, 0.8500624999999999), (28.6499375, 29.25, 0.6000624999999999)]
[(0.0, 1.3, 1.3)]
You took 3 short pauses and 1 long pause.
('Good work! You are doing well but can improve in reducing awkward pauses. When you have unexpected pauses then it can distract your audience. A pause can be powerful if it is planned well in speech such as an introduction (Here comes Mr. Akshay), or an exclamation (Wow!). However, unplanned pauses breaks your sentences in between and confuses your audience.', ['Good work!', 'You are doing well but can improve in reducing awkward pauses.', 'When you have unexpected pauses then it can distract your audience. A pause can be powerful if it is planned well in speech such as an introduction (Here comes Mr. Akshay), or an exclamation (Wow!). However, unplanned pauses breaks your sentences in betwee

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_115.wav
[(0.0, 0.8, 0.8), (11.3999375, 12.0, 0.6000624999999999)]
[]
You took 2 short pauses and 0 long pause.
('Good job! Work on your speech some more until you minimize the number of unexpected pauses you take. When you have unexpected pauses then it can distract your audience. A pause can be powerful if it is planned well in speech such as an introduction (Here comes Mr. Akshay), or an exclamation (Wow!). However, unplanned pauses breaks your sentences in between and confuses your audience.', ['Good job!', 'Work on your speech some more until you minimize the number of unexpected pauses you take.', 'When you have unexpected pauses then it can distract your audience. A pause can be powerful if it is planned well in speech such as an introduction (Here comes Mr. Akshay), or an exclamation (Wow!). However, unplanned pauses breaks your sentences in between and confuses your audienc

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_124.wav
[(0.0, 0.75, 0.75), (12.8999375, 13.55, 0.6500625000000007)]
[]
You took 2 short pauses and 0 long pause.
('Nice! Work on your speech some more until you minimize the number of unexpected pauses you take. When you have unexpected pauses then it can distract your audience. A pause can be powerful if it is planned well in speech such as an introduction (Here comes Mr. Akshay), or an exclamation (Wow!). However, unplanned pauses breaks your sentences in between and confuses your audience.', ['Nice!', 'Work on your speech some more until you minimize the number of unexpected pauses you take.', 'When you have unexpected pauses then it can distract your audience. A pause can be powerful if it is planned well in speech such as an introduction (Here comes Mr. Akshay), or an exclamation (Wow!). However, unplanned pauses breaks your sentences in between and confuses your audience.'])

...

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_70.wav
[(0.0, 0.55, 0.55)]
[]
You took 1 short pause and 0 long pause.
('Great job! With fewer awkward pauses the flow of your speech is not broken and its easy to understand. But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You will notice that there is often a pause before introducing Amitabh Bachhan in order to create suspense. Now you too practice introducing pauses purposefully to increase the quality of your speech.', ['Great job!', 'With fewer awkward pauses the flow of your speech is not broken and its easy to understand.', 'But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagi

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_77.wav
[(20.3499375, 20.95, 0.6000624999999999), (27.5999375, 28.3, 0.7000625000000014), (51.9499375, 52.5, 0.5500625000000028)]
[(0.0, 1.3, 1.3)]
You took 3 short pauses and 1 long pause.
('Great job! You really prepared your speech well as visible by your lack of awkward pauses. But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You will notice that there is often a pause before introducing Amitabh Bachhan in order to create suspense. Now you too practice introducing pauses purposefully to increase the quality of your speech.', ['Great job!', 'You really prepared your speech well as visible by your lack of awkward pauses.', 'But remember pauses are not all bad. Great speakers use pause for

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_84.wav
[]
[(0.0, 1.6, 1.6)]
You took 0 short pause and 1 long pause.
('Excellent! You are doing well in reducing awkward pauses. But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You will notice that there is often a pause before introducing Amitabh Bachhan in order to create suspense. Now you too practice introducing pauses purposefully to increase the quality of your speech.', ['Excellent!', 'You are doing well in reducing awkward pauses.', 'But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You wi

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_91.wav
[(0.0, 0.65, 0.65), (9.1999375, 9.8, 0.6000624999999999), (40.3499375, 40.85, 0.5000624999999985)]
[]
You took 3 short pauses and 0 long pause.
('Amazing work! With fewer awkward pauses the flow of your speech is not broken and its easy to understand. But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You will notice that there is often a pause before introducing Amitabh Bachhan in order to create suspense. Now you too practice introducing pauses purposefully to increase the quality of your speech.', ['Amazing work!', 'With fewer awkward pauses the flow of your speech is not broken and its easy to understand.', 'But remember pauses are not all bad. Great speakers use pause for introdu

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
[(0.0, 0.8, 0.8)]
[]
You took 1 short pause and 0 long pause.
('Great work! You are doing well in reducing awkward pauses. But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You will notice that there is often a pause before introducing Amitabh Bachhan in order to create suspense. Now you too practice introducing pauses purposefully to increase the quality of your speech.', ['Great work!', 'You are doing well in reducing awkward pauses.', 'But remember pauses are not all bad. Great speakers use pause for introducing dramatic effect and introduce smooth transitions between their speech. Just imagine an anchor on stage saying, "Please, welcome the one and only.... Amitabh Bachhan." You 

In [10]:
import IPython
IPython.display.Audio('/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_88.wav')

In [ ]:
pause_info, time_arr = pause_main(file_location)
short_pauses = [(i['pause_start'], i['pause_finish'], i['pause_duration']) for i in pause_info if (i['pause_duration']>=0.5 and i['pause_duration']<1)]
long_pauses = [(i['pause_start'], i['pause_finish'], i['pause_duration']) for i in pause_info if (i['pause_duration']>=1)]

pause_score = (1 - sum([i['pause_duration'] for i in pause_info])/time_arr[-1])*0.8
print(pause_score)

In [ ]:
time_arr[-1]

## Identify WPM

In [124]:
def pace_feedback(pace_score, articulation_rate):
    
    text = ''
    text_list = []
    if pace_score>=85:
        temp_lst = ['Great job!', 'Great work!', 'Excellent!', 'Bravo!', 'Amazing work!', 'Exemplary work!', 
                   ]
        
        random.shuffle(temp_lst)
        text += """{} Your pace is in recommended limit and will be easy to follow for most of your audience.""".format(temp_lst[0])
        text_list += [temp_lst[0], """Your pace is in recommended limit and will be easy to follow for most of your audience."""]
    
    elif pace_score>=60:
        temp_lst = ['Good job!', 'Good work!', 'Well done!', 'Nice!']
        random.shuffle(temp_lst)
        text += """{} Your pace needs more work to make it more interesting for the audience. Slow speaking overall bores the audience and their attention wanders away.""".format(temp_lst[0])
        text_list += [temp_lst[0], """Your pace needs more work to make it more interesting for the audience. Slow speaking overall bores the audience and their attention wanders away."""]
        
    elif pace_score<60:
        temp_lst = ['Satisfactory!', 'OK!', 'Not great!', 'You can do better!']
        random.shuffle(temp_lst)
        
        if articulation_rate>240:
            text += """{} Your pace is too fast for the audience to follow. Try practicing tongue twisters to slow yourself down which will make your enunciation better and clearer.""".format(temp_lst[0])
            text_list += [temp_lst[0], """Your pace is too fast for the audience to follow. Try practicing tongue twisters to slow yourself down which will make your enunciation better and clearer."""]
        else:
            text += """{} Your pace is too slow and dull which will lose audience attention. Speed up the pace by trying speed reading with speaking which will develop the muscular strength and skill to speak faster.""".format(temp_lst[0])
            text_list += [temp_lst[0], """Your pace is too slow and dull which will lose audience attention. Speed up the pace by trying speed reading with speaking which will develop the muscular strength and skill to speak faster."""]
        
    return text, text_list

In [125]:
def speech_rate(filename):
    cols = ['soundname', 'nsyll', 'npause', 'dur(s)', 'phonationtime(s)', 'speechrate(nsyll / dur)', 'articulation '
        'rate(nsyll / phonationtime)', 'ASD(speakingtime / nsyll)']
    
    silencedb = -25
    mindip = 2
    minpause = 0.3
    sound = parselmouth.Sound(filename)
    originaldur = sound.get_total_duration()
    intensity = sound.to_intensity(50)
    start = call(intensity, "Get time from frame number", 1)
    nframes = call(intensity, "Get number of frames")
    end = call(intensity, "Get time from frame number", nframes)
    min_intensity = call(intensity, "Get minimum", 0, 0, "Parabolic")
    max_intensity = call(intensity, "Get maximum", 0, 0, "Parabolic")

    # get .99 quantile to get maximum (without influence of non-speech sound bursts)
    max_99_intensity = call(intensity, "Get quantile", 0, 0, 0.99)

    # estimate Intensity threshold
    threshold = max_99_intensity + silencedb
    threshold2 = max_intensity - max_99_intensity
    threshold3 = silencedb - threshold2
    if threshold < min_intensity:
        threshold = min_intensity

    # get pauses (silences) and speakingtime
    textgrid = call(intensity, "To TextGrid (silences)", threshold3, minpause, 0.1, "silent", "sounding")
    silencetier = call(textgrid, "Extract tier", 1)
    silencetable = call(silencetier, "Down to TableOfReal", "sounding")
    npauses = call(silencetable, "Get number of rows")
    speakingtot = 0
    for ipause in range(npauses):
        pause = ipause + 1
        beginsound = call(silencetable, "Get value", pause, 1)
        endsound = call(silencetable, "Get value", pause, 2)
        speakingdur = endsound - beginsound
        speakingtot += speakingdur

    intensity_matrix = call(intensity, "Down to Matrix")
    # sndintid = sound_from_intensity_matrix
    sound_from_intensity_matrix = call(intensity_matrix, "To Sound (slice)", 1)
    # use total duration, not end time, to find out duration of intdur (intensity_duration)
    # in order to allow nonzero starting times.
    intensity_duration = call(sound_from_intensity_matrix, "Get total duration")
    intensity_max = call(sound_from_intensity_matrix, "Get maximum", 0, 0, "Parabolic")
    point_process = call(sound_from_intensity_matrix, "To PointProcess (extrema)", "Left", "yes", "no", "Sinc70")
    # estimate peak positions (all peaks)
    numpeaks = call(point_process, "Get number of points")
    t = [call(point_process, "Get time from index", i + 1) for i in range(numpeaks)]

    # fill array with intensity values
    timepeaks = []
    peakcount = 0
    intensities = []
    for i in range(numpeaks):
        value = call(sound_from_intensity_matrix, "Get value at time", t[i], "Cubic")
        if value > threshold:
            peakcount += 1
            intensities.append(value)
            timepeaks.append(t[i])

    # fill array with valid peaks: only intensity values if preceding
    # dip in intensity is greater than mindip
    validpeakcount = 0
    currenttime = timepeaks[0]
    currentint = intensities[0]
    validtime = []

    for p in range(peakcount - 1):
        following = p + 1
        followingtime = timepeaks[p + 1]
        dip = call(intensity, "Get minimum", currenttime, timepeaks[p + 1], "None")
        diffint = abs(currentint - dip)
        if diffint > mindip:
            validpeakcount += 1
            validtime.append(timepeaks[p])
        currenttime = timepeaks[following]
        currentint = call(intensity, "Get value at time", timepeaks[following], "Cubic")

    # Look for only voiced parts
    pitch = sound.to_pitch_ac(0.02, 30, 4, False, 0.03, 0.25, 0.01, 0.35, 0.25, 450)
    voicedcount = 0
    voicedpeak = []

    for time in range(validpeakcount):
        querytime = validtime[time]
        whichinterval = call(textgrid, "Get interval at time", 1, querytime)
        whichlabel = call(textgrid, "Get label of interval", 1, whichinterval)
        value = pitch.get_value_at_time(querytime) 
        if not math.isnan(value):
            if whichlabel == "sounding":
                voicedcount += 1
                voicedpeak.append(validtime[time])

    # calculate time correction due to shift in time for Sound object versus
    # intensity object
    timecorrection = originaldur / intensity_duration

    # Insert voiced peaks in TextGrid
    call(textgrid, "Insert point tier", 1, "syllables")
    for i in range(len(voicedpeak)):
        position = (voicedpeak[i] * timecorrection)
        call(textgrid, "Insert point", 1, position, "")

    # return results
    speakingrate = voicedcount / originaldur
    articulationrate = voicedcount / speakingtot
    npause = npauses - 1
    asd = speakingtot / voicedcount
    speechrate_dictionary = {'soundname':file,
                             'nsyll':voicedcount,
                             'npause': npause,
                             'dur(s)':originaldur,
                             'phonationtime(s)':intensity_duration,
                             'speechrate(nsyll / dur)': speakingrate,
                             "articulation rate(nsyll / phonationtime)":articulationrate,
                             "ASD(speakingtime / nsyll)":asd}
    return speechrate_dictionary


def compute_articulation_rate(file_location):
    try:
        speechrate_dictionary = speech_rate(file_location)
        articulation_rate = speechrate_dictionary['articulation rate(nsyll / phonationtime)']
    except:
        articulation_rate = 0
        
    return articulation_rate

In [126]:
def return_articulation_rate(file_location):
    
    articulation_rate = compute_articulation_rate(file_location)
    articulation_rate = articulation_rate*60
    
    return articulation_rate

In [117]:
for file_location in audio_files:
        
    print('------------')
    print(file_location)
    pace_score, articulation_rate = return_pace_score(file_location)
    print(pace_score, articulation_rate)

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_100.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
80.0 193.08312655086846
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_101.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
79.0 289.6356586724217
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_102.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
94.0 225.6944444444444
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_103.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
100.0 241.03535641733814
------------
/home/ubuntu/speechRecognition/vosk-

95.0 250.87190868738122
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_138.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
99.0 238.42233150906839
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_139.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
96.0 249.81074943224837
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_14.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
63.0 151.99894445177463
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_140.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
94.0 255.41182682154175
------------
/home/ubuntu

69.0 164.6258817476989
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_170.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
94.0 255.52702448800656
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_171.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
91.0 261.62790697674416
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_172.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
96.0 249.77032613688556
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_173.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
93.0 255.8580289455548
------------
/home/ubuntu/

84.0 201.49253731343282
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_207.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
90.0 264.0503875968992
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_208.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
80.0 191.95756727460247
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_209.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
85.0 275.5515777768737
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_21.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
95.0 227.79516231888357
------------
/home/ubuntu/s

83.0 280.88329225660345
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_24.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
96.0 229.6887128139927
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_240.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
88.0 212.26415094339606
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_241.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
91.0 217.89459349039902
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_242.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
98.0 234.77762931857222
------------
/home/ubuntu/

...

90.0 264.44662095984324
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_378.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
82.0 284.09090909090907
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_379.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
86.0 274.71834896452583
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_38.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
94.0 254.2469070409746
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_380.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
98.0 234.241202143528
------------
/home/ubuntu/sp

74.0 302.58288560261195
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_413.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
98.0 243.7002652519895
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_414.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
87.0 271.0843373493976
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_415.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
97.0 247.79289289329657
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_416.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
95.0 252.2107980298583
------------
/home/ubuntu/s

74.0 177.1620167404266
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_448.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
91.0 218.08202020574123
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_449.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
89.0 266.54064272211724
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_45.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
92.0 221.16644823066838
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_450.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
84.0 278.9115076139154
------------
/home/ubuntu/s

99.0 241.97839745325214
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_482.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
80.0 289.0173410404625
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_483.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
90.0 263.27002678354006
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_49.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
98.0 245.74776722225374
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_50.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
99.0 243.0898321816386
------------
/home/ubuntu/sp

76.0 181.2977099236641
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_81.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
88.0 210.56149732620315
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_82.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
72.0 306.81662532150295
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_83.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
91.0 217.39130434782615
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_84.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav
93.0 223.19827895302973
------------
/home/ubuntu/spe

In [118]:
def energy_feedback(energy_score):
    
    text = ''
    text_list = []
    if energy_score>=90:
        temp_lst = ['Great job!', 'Great work!', 'Excellent!', 'Bravo!', 'Amazing work!', 'Exemplary work!', 
                   ]
        temp_lst2 = ["Your energy is commendable.', 'Your voice carries energy and momentum that can catch people's attention .",
                    'Your power reflects the confidence you have in yourself and your preparation',
                    'Your energy is high and that is a good note to start a speech on.']
        random.shuffle(temp_lst)
        random.shuffle(temp_lst2)
        text += """{} {}. While a good energy is nice to have, being too loud will also turn off your audience. It is best to start with strong energy and then bring variation along with vocal variety. It would be best to start with high energy, then maintain a consistent, normal volume and soften up if the speech demands it such as when showing despair and grief.""".format(temp_lst[0], temp_lst2[0])
        text_list += [temp_lst[0], temp_lst2[0], """While a good energy is nice to have, being too loud will also turn off your audience. It is best to start with strong energy and then bring variation along with vocal variety. It would be best to start with high energy, then maintain a consistent, normal volume and soften up if the speech demands it such as when showing despair and grief."""]
    
    elif energy_score>=60:
        temp_lst = ['Good job!', 'Good work!', 'Well done!', 'Nice!']
        temp_lst2 = ['You are doing well but can still improve your overall energy.', 
                     'Your speaking voice is commanding but there is room for further improvement.',
                    "You can attract people's attention but with further practice you will be able to hold it for longer duration.",
                    "Your speaking voice has potential but with further practice it can be perfected for even live auditorium."]
        random.shuffle(temp_lst)
        random.shuffle(temp_lst2)
        text += """{} {}. Having a good power is a great way to start a speech as it catches audience attention and create a positive, energetic vibe. You can improve your energy by practicing taking long breaths and speaking out sounds such as Om, Do, Re, Me, Fa, So, La, Ti for extended periods of time.""".format(temp_lst[0], temp_lst2[0])
        text_list += [temp_lst[0], temp_lst2[0], """Having a good power is a great way to start a speech as it catches audience attention and create a positive, energetic vibe. You can improve your energy by practicing taking long breaths and speaking out sounds such as Om, Do, Re, Me, Fa, So, La, Ti for extended periods of time."""]
        
    elif energy_score<60:
        temp_lst = ['Satisfactory!', 'OK!', 'Not great!', 'You can do better!']
        temp_lst2 = ['Your needs further improvement as you would not be audible to many people.', 
                     "Your speech lacks the gravity to catch people's attention.",
                    'You should work more on to increasing the strength of throat muscle to improve your vocal strength.',
                    'Your voice is too soft and uninspiring at the moment.']
        random.shuffle(temp_lst)
        random.shuffle(temp_lst2)
        text += """{} {}. Speaking with energy is vital for audience engagement. A lot of power comes from your lungs and breathing. Try practicing breathing and speaking from your stomach which means always take deep breath to fill all your diaphragm. Beyond that speak out loud sounds such as Om, Do, Re, Me, Fa, So, La, Ti for extended periods of time.""".format(temp_lst[0], temp_lst2[0])
        text_list += [temp_lst[0], temp_lst2[0], """Speaking with energy is vital for audience engagement. A lot of power comes from your lungs and breathing. Try practicing breathing and speaking from your stomach which means always take deep breath to fill all your diaphragm. Beyond that speak out loud sounds such as Om, Do, Re, Me, Fa, So, La, Ti for extended periods of time."""]
        
    return text, text_list

In [119]:
def return_energy_score(file_location):

    snd = parselmouth.Sound(file_location)
    intensity = snd.to_intensity()
    item = intensity.values.T
    
    new_item = []
    for val in item:
        if (val>=50) and (val<=75):
            new_item.append(1)
        elif (val<50) and (val>=30):
            new_item.append(-1)
        elif val>75:
            new_item.append(2)
        else:
            new_item.append(0)
    
    energy_score = sum([i for i in new_item if i!=0])/(len([i for i in new_item if i!=0]))*100
    
    return energy_score

In [ ]:
for file_location in audio_files:
        
    print('------------')
    print(file_location)
    energy_score = return_energy_score(file_location)
    print(energy_score)

In [120]:
def return_pitch_score(file_location):

    snd = parselmouth.Sound(file_location)
    pitch = snd.to_pitch()
    pitch = pitch.selected_array['frequency']
    
    new_item = []
    for val in pitch:
        if (val>=200) and (val<=300):
            new_item.append(1)
        elif val<200:
            new_item.append(0)
        else:
            new_item.append(2)
            
    pitch_score =  sum(new_item)/(len(new_item))*100
    
    return pitch_score

In [121]:
def pitch_feedback(pitch_score):
    
    text = ''
    text_list = []
    if pitch_score>=90:
        temp_lst = ['Great job!', 'Great work!', 'Excellent!', 'Bravo!', 'Amazing work!', 'Exemplary work!', 
                   ]
        temp_lst2 = ['Your use of vocal variety is commendable.', 'Your intonation and emphasis is adding beauty to your speech.',
                    'Your vocal variety will make listener want to listen to you.',
                    'Your pitch variation helps in expanding the meaning behind your words.']
        random.shuffle(temp_lst)
        random.shuffle(temp_lst2)
        text += """{} {} Afterall, a good vocal variety helps in communicating clear message to your audience about your intention. This makes you more memorable as a speaker and makes it easy to follow the key message you are trying to emphasize. However, beware of too much vocal variation as that will appear phony and pretentious.""".format(temp_lst[0], temp_lst2[0])
        text_list += [temp_lst[0], temp_lst2[0], """Afterall, a good vocal variety helps in communicating clear message to your audience about your intention. This makes you more memorable as a speaker and makes it easy to follow the key message you are trying to emphasize. However, beware of too much vocal variation as that will appear phony and pretentious."""]
    
    elif pitch_score>=60:
        temp_lst = ['Good job!', 'Good work!', 'Well done!', 'Nice!']
        temp_lst2 = ['You are doing well but can improve your vocal variation.', 
                     'Your speech intonation is good because you are able to modify the pitch of your voice. Nonetheless, you can do better.',
                    'Your vocal variation deserves praise, but work on bringing more emotions into your speech to make it better.',
                    'Your speech can illustrate your emotions and thus meaning behind your words. However, record yourself and listen to improve your vocal variation even more.']
        random.shuffle(temp_lst)
        random.shuffle(temp_lst2)
        text += """{} {}. The level of vocal variety you can bring to your speech adds more life into your speech. It not only helps to illustrate your meaning better but also improves your overall tone which makes it pleasant for audience to listen to you.""".format(temp_lst[0], temp_lst2[0])
        text_list += [temp_lst[0], temp_lst2[0], """The level of vocal variety you can bring to your speech adds more life into your speech. It not only helps to illustrate your meaning better but also improves your overall tone which makes it pleasant for audience to listen to you."""]
        
    elif pitch_score<60:
        temp_lst = ['Satisfactory!', 'OK!', 'Not great!', 'You can do better!']
        temp_lst2 = ['You need to improve your vocal variation.', 
                     'Your speech yet lacks the variation and appeal to excite the audience to listen to you.',
                    'You should work more on to infusing emotions into your words to make it more exciting and less monotonous.',
                    'Your speaking style yet is quite montonous. Try practicing elongating your vowels and also try to infuse more emotions into your words.']
        random.shuffle(temp_lst)
        random.shuffle(temp_lst2)
        text += """{} {}. Having poor vocal range signifies lack of emotion and excitement in a speech. This can bore audience and lose them to stop listening. A good way to improve vocal variety is to practice your favorite movie dialogues especially which are emotional like patriotic movies. This will start to build your natural tendency to bring different flavors in your speech.""".format(temp_lst[0], temp_lst2[0])
        text_list += [temp_lst[0], temp_lst2[0], """Having poor vocal range signifies lack of emotion and excitement in a speech. This can bore audience and lose them to stop listening. A good way to improve vocal variety is to practice your favorite movie dialogues especially which are emotional like patriotic movies. This will start to build your natural tendency to bring different flavors in your speech."""]
        
    return text, text_list

In [ ]:
for file_location in audio_files:
        
    print('------------')
    print(file_location)
    pitch_score = return_pitch_score(file_location)
    print(pitch_score)

## Combined

In [127]:
output_arr = []

for file_location in audio_files:
    output_dict = {}
        
    print('------------')
    print(file_location)
    
    ## Pause Feedback
    pause_info, time_arr = pause_main(file_location)
    
    short_pauses = [(i['pause_start'], i['pause_finish'], i['pause_duration']) for i in pause_info if (i['pause_duration']>=0.5 and i['pause_duration']<1)]
    long_pauses = [(i['pause_start'], i['pause_finish'], i['pause_duration']) for i in pause_info if (i['pause_duration']>=1)]

    pause_score = int(np.round(((1 - sum([i['pause_duration'] for i in pause_info])/time_arr[-1]))*100))
    
    text, text_list = pause_feedback(pause_score)
    
    if len(short_pauses)<=1 and len(long_pauses)<=1:
        text += ' Overall, you took {} short pause and {} long pause.'.format(len(short_pauses), len(long_pauses))
    elif len(short_pauses)<=1:
        text += ' Overall, you took {} short pause and {} long pauses.'.format(len(short_pauses), len(long_pauses))
    elif len(long_pauses)<=1:
        text += ' Overall, you took {} short pauses and {} long pause.'.format(len(short_pauses), len(long_pauses))
    else:
        text += ' Overall, you took {} short pauses and {} long pauses.'.format(len(short_pauses), len(long_pauses))
        
    
    output_dict['Pause'] = {
        'Score': pause_score,
        'Text': text_list
    }
    
    ## Pace Feedback
    articulation_rate = return_articulation_rate(file_location)
    pace_score = np.round((1 - (abs(240-articulation_rate))/240)*100)
    
    text, text_list = pace_feedback(pace_score, articulation_rate)
    
    output_dict['Pace'] = {
        'Score': pace_score,
        'Text': text_list
    }
    
    ## Power Feedback
    energy_score = int(np.round(return_energy_score(file_location)))
    
    if energy_score>100: 
        energy_score = random.randint(90, 95)
        
    if energy_score<0:
        energy_score = random.randint(10, 20)
    
    text, text_list = energy_feedback(energy_score)
    
    output_dict['Power'] = {
        'Score': energy_score,
        'Text': text_list
    }
    
    ## Pitch Feedback
    pitch_score = int(np.round(return_pitch_score(file_location)))
    text, text_list = pitch_feedback(pitch_score)
    
    if pitch_score>100: 
        pitch_score = random.randint(90, 95)
        
    if pitch_score<0:
        pitch_score = random.randint(10, 20)
    
    output_dict['Pitch'] = {
        'Score': pitch_score,
        'Text': text_list
    }
    
    output_arr.append(output_dict)

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_100.wav


/home/ubuntu/miniconda3/envs/python_main/lib/python3.6/site-packages/ipykernel_launcher.py:42: RuntimeWarning: invalid value encountered in true_divide


------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_101.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_102.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_103.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_104.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_105.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_106.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_107.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_108.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/qu

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_172.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_173.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_174.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_176.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_178.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_179.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_180.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_181.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/qu

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_243.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_244.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_245.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_246.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_247.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_248.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_249.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_25.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/que

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_314.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_315.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_316.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_317.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_318.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_319.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_32.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_320.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/que

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_385.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_386.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_387.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_388.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_389.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_390.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_391.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_392.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/qu

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_458.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_459.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_46.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_460.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_461.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_462.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_463.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_464.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/que

------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_93.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_94.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_95.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_96.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_97.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_98.wav
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_99.wav


In [128]:
output_arr[8]

{'Pause': {'Score': 88,
  'Text': ['Well done!',
   'Work on your speech some more until you minimize the number of unexpected pauses you take.',
   'When you have unexpected pauses then it can distract your audience. A pause can be powerful if it is planned well in speech such as an introduction (Here comes Mr. Akshay), or an exclamation (Wow!). However, unplanned pauses breaks your sentences in between and confuses your audience.']},
 'Pace': {'Score': 96.0,
  'Text': ['Excellent!',
   'Your pace is in recommended limit and will be easy to follow for most of your audience.']},
 'Power': {'Score': 53,
  'Text': 'Satisfactory! Your needs further improvement as you would not be audible to many people.. Speaking with energy is vital for audience engagement. A lot of power comes from your lungs and breathing. Try practicing breathing and speaking from your stomach which means always take deep breath to fill all your diaphragm. Beyond that speak out loud sounds such as Om, Do, Re, Me, Fa, 

In [ ]:
2+2

In [22]:
'''Using librosa'''
# /home/ubuntu/audiospodcast_28420.wav
import librosa
from scipy.io import wavfile
fs, data = wavfile.read("/home/ubuntu/pause_audios/wav/podcast_15150.wav")
data = data.astype(np.float32)
zz = librosa.beat.beat_track(data, fs)

for file_location in audio_files:
        
    print('------------')
    print(file_location)
    fs, data = wavfile.read(file_location)
    data = data.astype(np.float32)
    zz = librosa.beat.beat_track(data, fs)
    
    print(zz[0])

/home/ubuntu/miniconda3/envs/python_main/lib/python3.6/site-packages/ipykernel_launcher.py:5: WavFileWarning: Chunk (non-data) not understood, skipping it.
  """


------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_100.wav
89.28571428571429
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_101.wav


/home/ubuntu/miniconda3/envs/python_main/lib/python3.6/site-packages/librosa/filters.py:239: UserWarning: Empty filters detected in mel frequency basis. Some channels will produce empty responses. Try increasing your sampling rate (and fmax) or reducing n_mels.
  "Empty filters detected in mel frequency basis. "


133.92857142857142
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_102.wav
117.1875
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_103.wav
125.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_104.wav
133.92857142857142
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_105.wav
133.92857142857142
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_106.wav
117.1875
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_107.wav
98.6842105263158
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_108.wav
133.92857142857142
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios

125.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_166.wav
93.75
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_167.wav
110.29411764705883
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_168.wav
75.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_169.wav
170.45454545454547
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_17.wav
133.92857142857142
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_170.wav
104.16666666666667
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_171.wav
125.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submissio

125.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_230.wav
144.23076923076923
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_231.wav
125.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_232.wav
89.28571428571429
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_233.wav
110.29411764705883
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_235.wav
110.29411764705883
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_236.wav
125.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_237.wav
133.92857142857142
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/ques

187.5
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_295.wav
117.1875
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_296.wav
117.1875
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_297.wav
133.92857142857142
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_298.wav
234.375
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_299.wav
170.45454545454547
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_30.wav
78.125
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_300.wav
104.16666666666667
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_3

110.29411764705883
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_359.wav
125.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_36.wav
110.29411764705883
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_360.wav
93.75
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_361.wav
170.45454545454547
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_362.wav
125.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_363.wav
81.52173913043478
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_364.wav
170.45454545454547
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/quest

98.6842105263158
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_423.wav
98.6842105263158
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_424.wav
133.92857142857142
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_425.wav
117.1875
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_426.wav
110.29411764705883
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_427.wav
117.1875
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_428.wav
98.6842105263158
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_429.wav
125.0
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/que

117.1875
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_54.wav
133.92857142857142
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_55.wav
93.75
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_56.wav
98.6842105263158
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_57.wav
144.23076923076923
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_58.wav
117.1875
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_59.wav
117.1875
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_6.wav
104.16666666666667
------------
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submissi

In [20]:
zz[0]

112.34714673913044

In [29]:
import IPython
IPython.display.Audio("/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_361.wav")

/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_100.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_101.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_102.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_103.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_104.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_105.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_106.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_107.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_108.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submissio

/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_183.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_184.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_185.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_186.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_188.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_189.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_19.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_190.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_191.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission

/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_261.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_262.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_263.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_265.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_266.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_267.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_268.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_27.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_270.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission

/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_343.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_344.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_345.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_346.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_347.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_348.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_349.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_35.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_350.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission

/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_425.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_426.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_427.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_428.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_429.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_430.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_431.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_432.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_433.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submissio

/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_71.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_72.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_73.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_74.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_75.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_76.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_77.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_78.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_79.wav
/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_8.wav
/

In [77]:
df = pd.DataFrame(datalist)
df = df.drop_duplicates(subset = ['soundname'])
df

soundname  nsyll  npause  \
0    /home/ubuntu/speechRecognition/vosk-api/python...     83       5   
1    /home/ubuntu/speechRecognition/vosk-api/python...    111       1   
2    /home/ubuntu/speechRecognition/vosk-api/python...     26       2   
3    /home/ubuntu/speechRecognition/vosk-api/python...     11       0   
4    /home/ubuntu/speechRecognition/vosk-api/python...     59       0   
..                                                 ...    ...     ...   
580  /home/ubuntu/speechRecognition/vosk-api/python...    137       4   
581  /home/ubuntu/speechRecognition/vosk-api/python...    117       7   
582  /home/ubuntu/speechRecognition/vosk-api/python...     37       0   
583  /home/ubuntu/speechRecognition/vosk-api/python...     16       0   
584  /home/ubuntu/speechRecognition/vosk-api/python...     39       4   

        dur(s)  phonationtime(s)  speechrate(nsyll / dur)  \
0    30.511063         30.511063                 2.720325   
1    24.148812         24.148812                 4.596499   
2    12.213750         12.213750                 2.128748   
3     3.204375          3.204375                 3.432807   
4    15.232313         15.232313                 3.873345   
..         ...               ...                      ...   
580  35.155062         35.155062                 3.897021   
581  30.743250         30.743250                 3.805713   
582   8.080500          8.080500                 4.578925   
583   4.040312          4.040312                 3.960090   
584  14.024875         14.024875                 2.780773   

     articulation rate(nsyll / phonationtime)  ASD(speakingtime / nsyll)  
0                                    3.218052                   0.310747  
1                                    4.827261                   0.207157  
2                                    3.761574                   0.265846  
3                                    4.017256                   0.248926  
4                                    4.238506                   0.235932  
..                                        ...                        ...  
580                                  4.240760                   0.235807  
581                                  4.433897                   0.225535  
582                                  5.267466                   0.189845  
583                                  3.960090                   0.252520  
584                                  4.145408                   0.241231  

[440 rows x 8 columns]

In [90]:
sorted([(i, i*60) for i in df['articulation rate(nsyll / phonationtime)'].tolist()])

[(1.0221421544201261, 61.328529265207564),
 (1.266624445851805, 75.9974667511083),
 (1.3457818151232233, 80.74690890739339),
 (1.3686131386861315, 82.11678832116789),
 (1.5880105205696988, 95.28063123418193),
 (1.794325445777728, 107.65952674666369),
 (1.910480349344978, 114.62882096069868),
 (2.311804652506863, 138.70827915041178),
 (2.447137995641035, 146.8282797384621),
 (2.5116950802172617, 150.7017048130357),
 (2.5333157408629106, 151.99894445177463),
 (2.5943281500818833, 155.659689004913),
 (2.5963629282646554, 155.78177569587933),
 (2.604166666666666, 156.24999999999997),
 (2.6041666666666665, 156.25),
 (2.7247956403269757, 163.48773841961855),
 (2.734375, 164.0625),
 (2.7437646957949817, 164.6258817476989),
 (2.8234712814736165, 169.408276888417),
 (2.834524774205825, 170.0714864523495),
 (2.854538755405589, 171.27232532433533),
 (2.893145730914844, 173.58874385489062),
 (2.9033611698126047, 174.20167018875628),
 (2.95270027900711, 177.1620167404266),
 (2.968913726859936, 178.

In [106]:
df[df['articulation rate(nsyll / phonationtime)']==5.646755969835528].to_dict(orient = 'records')

[{'soundname': '/home/ubuntu/speechRecognition/vosk-api/python/example/submission_audios/question_submission_147.wav',
  'nsyll': 34,
  'npause': 0,
  'dur(s)': 6.3623125,
  'phonationtime(s)': 6.3623125,
  'speechrate(nsyll / dur)': 5.343968879240056,
  'articulation rate(nsyll / phonationtime)': 5.646755969835528,
  'ASD(speakingtime / nsyll)': 0.17709283088235295}]

In [85]:
emotional_files

['/home/ubuntu/emotional_sounds/wav/Dr_Evil_Laughing_Scene.wav',
 "/home/ubuntu/emotional_sounds/wav/Will's_Father_leaves.wav",
 '/home/ubuntu/emotional_sounds/wav/The_Great_Dictator.wav']

In [ ]:
## Old strategy to compute pace

# def return_wpm(file_location, model):
    
#     # Large vocabulary free form recognition
#     rec = KaldiRecognizer(model, 16000)

#     # You can also specify the possible word list
#     #rec = KaldiRecognizer(model, 16000, "zero oh one two three four five six seven eight nine")
#     wf = open(file_location, "rb")
#     wf.read(44) # skip header

#     transcription = ""
#     while True:
#         data = wf.read(4000)
#         if len(data) == 0:
#             break
#         if rec.AcceptWaveform(data):
#             res = json.loads(rec.Result())
#             transcription += " " + res['text']
#     words = transcription.split(" ")

#     Fs, data = wavfile.read(file_location)
#     n = data.size
#     duration = round(n / Fs)
#     wpm = round(len(words)*60/duration)
    
#     return len(words), duration, wpm

In [107]:
## Automatic writing of bash script, starting bash script from python directly

# num_range = 20 # len(os.listdir('temp_dir/'))

# text = '#! /bin/bash\n\n'
# kill_text = '#! /bin/bash\n\n'
# for num in range(0, num_range, 1000): #
#     speech_trans = 'speech_trans_' + str(num)
#     send_keys_suffix = '"conda activate python_main"' + ' Enter ' + '"python3.6 translation_support.py' + ' ' + str(num) +' ' + str(num+1000) + '" ' + 'Enter'
#     text += 'tmux new-session -d -s '+ speech_trans +' \; send-keys ' + send_keys_suffix + '\n'
#     kill_text += 'tmux kill-session -t ' + speech_trans + '\n'

# with open('run_speech.sh', 'w') as f:
#     f.write(text)
    
# with open('kill_speech.sh', 'w') as f:
#     f.write(kill_text)
    
    
# import subprocess

# bashCommand = "chmod +x run_speech.sh"
# process = subprocess.Popen(bashCommand.split(), stdout=subprocess.PIPE)
# output, error = process.communicate()

# bashCommand = "sh run_speech.sh"
# process = subprocess.Popen(bashCommand, stdout=subprocess.PIPE, shell = True)
# output, error = process.communicate()

# import subprocess

# bashCommand = "chmod +x kill_speech.sh"
# process = subprocess.Popen(bashCommand.split(), stdout=subprocess.PIPE)
# output, error = process.communicate()

# bashCommand = "./kill_speech.sh"
# process = subprocess.Popen(bashCommand.split(), stdout=subprocess.PIPE)